In [1]:
from shapely.geometry import Point
import geopandas as gpd
import pandas as pd
import matplotlib.pyplot as plt
import requests
import json
import folium
from folium.plugins import MarkerCluster
from folium.plugins import FastMarkerCluster
from geopy.geocoders import Nominatim
%matplotlib inline 

In [2]:
crashes_df = gpd.read_file('data/crashes_cleaned.geojson')

In [3]:
crashes_df.set_crs(crs='EPSG:4326', inplace=True)

injuries_fatal  injuries_non_incapacitating  \
0                  NaN                          NaN   
1                  0.0                          0.0   
2                  NaN                          NaN   
3                  0.0                          0.0   
4                  0.0                          0.0   
...                ...                          ...   
631400             0.0                          0.0   
631401             0.0                          0.0   
631402             0.0                          1.0   
631403             0.0                          0.0   
631404             0.0                          0.0   

                                          crash_record_id  \
0       0edc78f89df5b72ddaa1c1f567e229ad39c0e098953a9d...   
1       49ff3f04d16f5a71e6d66436c94f6acfd939c20d6c3651...   
2       e580e89f187525bf685101a36fc64df499a72be926d5a9...   
3       cdd7c5d90668e4d1bda12805ad19cec305667643a88806...   
4       e7c26ad2dd7f250b14acafe2d86265616f59f7c642a505...   
...                                                   ...   
631400  964aaaeb569e364886cfbdf89ca73e09ca15cd916d87b2...   
631401  1d0232afecbdfd01968555aa956a688fd6f55a2bd1984f...   
631402  957783a4787318f005a7dbc920e4c84cb9ac8aa7329a62...   
631403  f62e27317feb174811cf4fefeb9fa1064fea6c0619a873...   
631404  a802658be15312809c771559e4f81088cfb226830792a5...   

        injuries_incapacitating  injuries_no_indication      latitude  \
0                           NaN                     NaN  41.873520168   
1                           0.0                     2.0  41.831835811   
2                           NaN                     NaN  41.838371536   
3                           0.0                     1.0  41.861481407   
4                           0.0                     2.0  41.837964154   
...                         ...                     ...           ...   
631400                      0.0                     2.0  41.835886103   
631401                      0.0                     2.0  41.884016475   
631402                      0.0                     1.0  41.760710194   
631403                      0.0                     2.0  41.885609917   
631404                      0.0                     1.0  41.975856916   

       street_no  injuries_unknown      device_condition           crash_date  \
0           3357               NaN           NO CONTROLS  2022-08-09T01:40:00   
1           3410               0.0  FUNCTIONING PROPERLY  2022-08-09T00:45:00   
2            130               NaN  FUNCTIONING PROPERLY  2022-08-08T23:55:00   
3           2747               0.0           NO CONTROLS  2022-08-08T23:00:00   
4           3100               0.0  FUNCTIONING PROPERLY  2022-08-08T23:00:00   
...          ...               ...                   ...                  ...   
631400      3132               0.0           NO CONTROLS  2014-06-25T19:00:00   
631401       199               0.0  FUNCTIONING PROPERLY  2014-02-24T19:45:00   
631402      7400               0.0           NO CONTROLS  2014-01-21T07:40:00   
631403       415               0.0           NO CONTROLS  2014-01-18T18:14:00   
631404      3200               0.0  FUNCTIONING PROPERLY  2013-03-03T16:48:00   

        ...                 prim_contributory_cause  \
0       ...  FAILING TO REDUCE SPEED TO AVOID CRASH   
1       ...                   FOLLOWING TOO CLOSELY   
2       ...           FAILING TO YIELD RIGHT-OF-WAY   
3       ...                     UNABLE TO DETERMINE   
4       ...            DISREGARDING TRAFFIC SIGNALS   
...     ...                                     ...   
631400  ...             IMPROPER OVERTAKING/PASSING   
631401  ...                     UNABLE TO DETERMINE   
631402  ...           FAILING TO YIELD RIGHT-OF-WAY   
631403  ...                     UNABLE TO DETERMINE   
631404  ...                     IMPROPER LANE USAGE   

              sec_contributory_cause street_direction posted_speed_limit  \
0                     NOT A

In [21]:
crashes_df.columns

Index(['injuries_fatal', 'injuries_non_incapacitating', 'crash_record_id',
       'injuries_incapacitating', 'injuries_no_indication', 'latitude',
       'street_no', 'injuries_unknown', 'device_condition', 'crash_date',
       'trafficway_type', 'traffic_control_device', 'road_defect', 'longitude',
       'crash_month', 'street_name', 'crash_day_of_week', 'crash_hour',
       'first_crash_type', 'injuries_reported_not_evident',
       'most_severe_injury', 'prim_contributory_cause',
       'sec_contributory_cause', 'street_direction', 'posted_speed_limit',
       'injuries_total', 'lane_cnt', 'full_address', 'no_significant_injury',
       'injuries_not_significant', 'geometry'],
      dtype='object')

In [5]:
peds_df = pd.read_csv('data/peds_cleaned_df.csv')

In [28]:
peds_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 15308 entries, 0 to 15307
Data columns (total 24 columns):
 #   Column                 Non-Null Count  Dtype  
---  ------                 --------------  -----  
 0   Unnamed: 0             15308 non-null  int64  
 1   person_id              15308 non-null  object 
 2   person_type            15308 non-null  object 
 3   crash_record_id        15308 non-null  object 
 4   crash_date             15308 non-null  object 
 5   city                   14180 non-null  object 
 6   state                  14035 non-null  object 
 7   zipcode                10585 non-null  object 
 8   sex                    15151 non-null  object 
 9   age                    14083 non-null  float64
 10  safety_equipment       12350 non-null  object 
 11  injury_classification  15308 non-null  object 
 12  hospital               10892 non-null  object 
 13  ems_agency             9289 non-null   object 
 14  driver_action          13524 non-null  object 
 15  dr

In [7]:
cyclists_df = pd.read_csv('data/cyclists_cleaned_df.csv')

In [8]:
cyclists_df

Unnamed: 0 person_id person_type  \
0              0  O1395052     BICYCLE   
1              1  O1394929     BICYCLE   
2              2  O1394880     BICYCLE   
3              3  O1394456     BICYCLE   
4              4  O1394398     BICYCLE   
...          ...       ...         ...   
9470        9470      O676     BICYCLE   
9471        9471      O464     BICYCLE   
9472        9472      O413     BICYCLE   
9473        9473      O967     BICYCLE   
9474        9474      O376     BICYCLE   

                                        crash_record_id  \
0     73c7c72402a0325ee3217b85b97f1cd880dce1e273294e...   
1     e7b51330cb3cffbe562d80eb7d25cce413dcf4d3d6f8f2...   
2     8fda3f8d995b2c9ba0cd7cbe35f60aacd6708defbd91db...   
3     e5bb72ff7b983e5d06b7419143e5bf9a6f6028c84cb0de...   
4     37a4a38e3879c073141bbe1259d755e6c9706c732e77c6...   
...                                                 ...   
9470  0ebcfc991b206474cf68ef0099609684dffb3b0c1e078e...   
9471  a2458d8a19e7f502ec81f85ecdbd971c1e4bb12dc34da8...   
9472  3d25ae31f7adea360bd4b6fb138c541a84443dae0fad58...   
9473  960536ce2853fdd8c904e8ed3ae0ba186535e0049a999b...   
9474  a7605090a223817b0b083b884e4b6914d7a47824a91793...   

                   crash_date  sex safety_equipment           ejection  \
0     2022-08-08T16:35:00.000    M  HELMET NOT USED  PARTIALLY EJECTED   
1     2022-08-08T14:12:00.000  NaN  HELMET NOT USED            UNKNOWN   
2     2022-08-08T13:00:00.000    M  HELMET NOT USED               NONE   
3     2022-08-07T19:35:00.000    M  HELMET NOT USED               NONE   
4     2022-08-07T17:19:00.000    M  HELMET NOT USED            UNKNOWN   
...                       ...  ...              ...                ...   
9470  2015-08-26T08:41:00.000    M  HELMET NOT USED    TOTALLY EJECTED   
9471  2015-08-21T09:30:00.000    M      HELMET USED  PARTIALLY EJECTED   
9472  2015-08-19T18:45:00.000    M      HELMET USED               NONE   
9473  2015-08-19T09:15:00.000    M      HELMET USED    TOTALLY EJECTED   
9474  2015-08-18T13:30:00.000    M    USAGE UNKNOWN            UNKNOWN   

         injury_classification                driver_action  ...  \
0        NO SIGNIFICANT INJURY  DISREGARDED CONTROL DEVICES  ...   
1        NO SIGNIFICANT INJURY               WRONG WAY/SIDE  ...   
2        NO SIGNIFICANT INJURY                IMPROPER TURN  ...   
3     NONINCAPACITATING INJURY              FAILED TO YIELD  ...   
4     NONINCAPACITATING INJURY                         NONE  ...   
...                        ...                          ...  ...   
9470     NO SIGNIFICANT INJURY                         NONE  ...   
9471  NONINCAPACITATING INJURY                          NaN  ...   
9472     NO SIGNIFICANT INJURY                        OTHER  ...   
9473     NO SIGNIFICANT INJURY                      UNKNOWN  ...   
9474  NONINCAPACITATING INJURY                      UNKNOWN  ...   

            bac_result     city state        hospital zipcode   age  \
0     TEST NOT OFFERED      NaN   NaN             NaN     NaN   NaN   
1     TEST NOT OFFERED      NaN   NaN             NaN     NaN   NaN   
2     TEST NOT OFFERED      NaN   NaN             NaN     NaN   NaN   
3     TEST NOT OFFERED  CHICAGO    IL  SELF TRANSPORT     NaN   NaN   
4     TEST NOT OFFERED  CHICAGO    IL   ST. BERNARD'S   60621  19.0   
...                ...      ...   ...             ...     ...   ...   
9470  TEST NOT OFFERED  CHICAGO    IL             NaN   60614  27.0   
9471  TEST NOT OFFERED  CHICAGO    IL             NaN   60622  52.0   
9472  TEST NOT OFFERED  CHICAGO    IL             NaN   60605  31.0   
9473  TEST NOT OFFERED  CHICAGO    IL             NaN   60647  33.0   
9474  TEST NOT OFFERED      NaN   NaN             NaN     NaN   NaN   

       ems_agency     rd_no bac_result_value cell_phone_use  
0             NaN       NaN              NaN            NaN  
1             NaN       NaN              NaN            NaN  
2             NaN       NaN              NaN   

# mapping crashes on folium map

## merge columns like pedpedal_location and pedpedal_action from people to be able to display on map popup?

## generate 4 dfs for peds by injury classification

In [14]:
peds_fatal_df = peds_df.loc[peds_df['injury_classification'] == 'FATAL']
print(peds_fatal_df.shape)

peds_incapacitating_df = peds_df.loc[peds_df['injury_classification'] == 'INCAPACITATING INJURY']
print(peds_incapacitating_df.shape)

peds_nonincapacitating_df = peds_df.loc[peds_df['injury_classification'] == 'NONINCAPACITATING INJURY']
print(peds_nonincapacitating_df.shape)

peds_no_significant_injury_df = peds_df.loc[peds_df['injury_classification'] == 'NO SIGNIFICANT INJURY']
print(peds_no_significant_injury_df.shape)

(191, 24)
(2575, 24)
(8075, 24)
(4467, 24)


## extract crash_record_ids from peds_dfs and filter crashes_df to create 4 dfs for crashes by injury classification
### didn't do nonincapacitating or no signif injury yet
### there could actually be duplicate geometries here b/c 2 peds in people would have same crash_record_id if there were 2 peds in crash ***ACTUALLY no there wouldn't b/c we're filtering, not joining

## peds fatal map

In [29]:
crash_id_peds_fatal = peds_fatal_df['crash_record_id'].tolist()
crashes_ped_fatal_df = crashes_df.loc[crashes_df['crash_record_id'].isin(crash_id_peds_fatal)].reset_index(drop=True)
crashes_ped_fatal_df.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 179 entries, 0 to 178
Data columns (total 31 columns):
 #   Column                         Non-Null Count  Dtype   
---  ------                         --------------  -----   
 0   injuries_fatal                 179 non-null    float64 
 1   injuries_non_incapacitating    179 non-null    float64 
 2   crash_record_id                179 non-null    object  
 3   injuries_incapacitating        179 non-null    float64 
 4   injuries_no_indication         179 non-null    float64 
 5   latitude                       178 non-null    object  
 6   street_no                      179 non-null    object  
 7   injuries_unknown               179 non-null    float64 
 8   device_condition               179 non-null    object  
 9   crash_date                     179 non-null    object  
 10  trafficway_type                179 non-null    object  
 11  traffic_control_device         179 non-null    object  
 12  road_defect                 

In [18]:
area_center = [41.881288,-87.686729]
ped_fatal_cluster_map = folium.Map(location =  area_center, zoom_start = 11)
marker_cluster = MarkerCluster().add_to(ped_fatal_cluster_map)
#folium.GeoJson(crashes_fatal_df).add_to(fatal_cluster_map)

for row_index, row_values in crashes_ped_fatal_df.iterrows():
    loc = (row_values['geometry'].y, row_values['geometry'].x)
    pop = row_values['trafficway_type'], row_values['traffic_control_device'],row_values['crash_date']
    icon=folium.Icon(color="blue",icon='user', prefix='fa')
    
    marker = folium.Marker(
        location = loc, 
        popup = pop,
    icon = icon)
    
    marker.add_to(marker_cluster)


ped_fatal_cluster_map

## peds_incapacitating map

In [30]:
crash_id_peds_incapacitating = peds_incapacitating_df['crash_record_id'].tolist()
crashes_ped_incapacitating_df = crashes_df.loc[crashes_df['crash_record_id'].isin(crash_id_peds_incapacitating)].reset_index(drop=True)
crashes_ped_incapacitating_df.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 2453 entries, 0 to 2452
Data columns (total 31 columns):
 #   Column                         Non-Null Count  Dtype   
---  ------                         --------------  -----   
 0   injuries_fatal                 2453 non-null   float64 
 1   injuries_non_incapacitating    2453 non-null   float64 
 2   crash_record_id                2453 non-null   object  
 3   injuries_incapacitating        2453 non-null   float64 
 4   injuries_no_indication         2453 non-null   float64 
 5   latitude                       2449 non-null   object  
 6   street_no                      2453 non-null   object  
 7   injuries_unknown               2453 non-null   float64 
 8   device_condition               2453 non-null   object  
 9   crash_date                     2453 non-null   object  
 10  trafficway_type                2453 non-null   object  
 11  traffic_control_device         2453 non-null   object  
 12  road_defect               

In [20]:
area_center = [41.881288,-87.686729]
ped_incapacitating_cluster_map = folium.Map(location =  area_center, zoom_start = 11)
marker_cluster = MarkerCluster().add_to(ped_incapacitating_cluster_map)
#folium.GeoJson(crashes_fatal_df).add_to(fatal_cluster_map)

for row_index, row_values in crashes_ped_incapacitating_df.iterrows():
    loc = (row_values['geometry'].y, row_values['geometry'].x)
    pop = row_values['trafficway_type'], row_values['traffic_control_device'],row_values['crash_date']
    icon=folium.Icon(color="blue",icon='user', prefix='fa')
    
    marker = folium.Marker(
        location = loc, 
        popup = pop,
    icon = icon)
    
    marker.add_to(marker_cluster)


ped_incapacitating_cluster_map

## generate 4 dfs for cyclists by injury classification

In [22]:
cyclists_fatal_df = cyclists_df.loc[cyclists_df['injury_classification'] == 'FATAL']
print(cyclists_fatal_df.shape)

cyclists_incapacitating_df = cyclists_df.loc[cyclists_df['injury_classification'] == 'INCAPACITATING INJURY']
print(cyclists_incapacitating_df.shape)

cyclists_nonincapacitating_df = cyclists_df.loc[cyclists_df['injury_classification'] == 'NONINCAPACITATING INJURY']
print(cyclists_nonincapacitating_df.shape)

cyclists_no_significant_injury_df = cyclists_df.loc[cyclists_df['injury_classification'] == 'NO SIGNIFICANT INJURY']
print(cyclists_no_significant_injury_df.shape)

(29, 25)
(862, 25)
(4556, 25)
(4026, 25)


## extract crash_record_ids from cyclists_dfs and filter crashes_df to create 4 dfs for crashes by injury classification

## cyclist fatal map

In [23]:
crash_id_cyclists_fatal = cyclists_fatal_df['crash_record_id'].tolist()
crashes_cyclist_fatal_df = crashes_df.loc[crashes_df['crash_record_id'].isin(crash_id_cyclists_fatal)].reset_index(drop=True)
crashes_cyclist_fatal_df.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 29 entries, 0 to 28
Data columns (total 31 columns):
 #   Column                         Non-Null Count  Dtype   
---  ------                         --------------  -----   
 0   injuries_fatal                 29 non-null     float64 
 1   injuries_non_incapacitating    29 non-null     float64 
 2   crash_record_id                29 non-null     object  
 3   injuries_incapacitating        29 non-null     float64 
 4   injuries_no_indication         29 non-null     float64 
 5   latitude                       29 non-null     object  
 6   street_no                      29 non-null     object  
 7   injuries_unknown               29 non-null     float64 
 8   device_condition               29 non-null     object  
 9   crash_date                     29 non-null     object  
 10  trafficway_type                29 non-null     object  
 11  traffic_control_device         29 non-null     object  
 12  road_defect                   

In [27]:
area_center = [41.881288,-87.686729]
cyclist_fatal_cluster_map = folium.Map(location =  area_center, zoom_start = 11)
marker_cluster = MarkerCluster().add_to(cyclist_fatal_cluster_map)
#folium.GeoJson(crashes_fatal_df).add_to(fatal_cluster_map)

for row_index, row_values in crashes_cyclist_fatal_df.iterrows():
    loc = (row_values['geometry'].y, row_values['geometry'].x)
    pop = row_values['trafficway_type'], row_values['traffic_control_device'],row_values['crash_date']
    icon=folium.Icon(color="blue",icon='bicycle', prefix='fa')
    
    marker = folium.Marker(
        location = loc, 
        popup = pop,
    icon = icon)
    
    marker.add_to(marker_cluster)


cyclist_fatal_cluster_map

## cyclist incapacitating map

In [24]:
#why does this go down from 854 to 834?
crash_id_cyclists_incapacitating = cyclists_incapacitating_df['crash_record_id'].tolist()
crashes_cyclist_incapacitating_df = crashes_df.loc[crashes_df['crash_record_id'].isin(crash_id_cyclists_incapacitating)].reset_index(drop=True)
crashes_cyclist_incapacitating_df.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 844 entries, 0 to 843
Data columns (total 31 columns):
 #   Column                         Non-Null Count  Dtype   
---  ------                         --------------  -----   
 0   injuries_fatal                 844 non-null    float64 
 1   injuries_non_incapacitating    844 non-null    float64 
 2   crash_record_id                844 non-null    object  
 3   injuries_incapacitating        844 non-null    float64 
 4   injuries_no_indication         844 non-null    float64 
 5   latitude                       842 non-null    object  
 6   street_no                      844 non-null    object  
 7   injuries_unknown               844 non-null    float64 
 8   device_condition               844 non-null    object  
 9   crash_date                     844 non-null    object  
 10  trafficway_type                844 non-null    object  
 11  traffic_control_device         844 non-null    object  
 12  road_defect                 